# Installing Dependencies

In [ ]:
pip install requests

In [ ]:
pip install pyspark

This project is meant to provide an idea of scraping instagram data from the internet and teach on how to perform image analysis for an instagram post. For this project, let's analyze the reels associated with Valorant community and see the user sentiments

# Scraping from Instagram

Setting up the RAPIDAPI for Instagram scraping the posts data from Instagram

In [ ]:
import pandas as pd
import requests
import json
import datetime
from datetime import datetime

In [ ]:
instagram_url = "https://instagram-scraper-api2.p.rapidapi.com/v1/search_reels"
instagram_post_scraping_header = {
	"x-rapidapi-key": "<your-api-key>",
	"x-rapidapi-host": "instagram-scraper-api2.p.rapidapi.com"
}

#Function to extract the reels from the API and then a subfunction call to get the data optimised for later execution

In [ ]:
def reels_extract(reel_topic):
    instagram_querystring = {'search_query' : reel_topic}
    response = requests.get(instagram_url, headers= instagram_post_scraping_header, params= instagram_querystring)
    if response.status_code == 200:
        reels_data = response.json()
        reels_data = reels_data['data']['items']
    reels_data = data_optimise_for_reels(reels_data)
    return reels_data

#Subfunction for reels data optimisation and Function call

In [ ]:
def data_optimise_for_reels(reels_data):
  df = pd.DataFrame()

  for i in range(0,len(reels_data)):
    reels_data_optimised = {}
    #Getting the reel shortcode
    reels_data_optimised['shortcode'] = reels_data[i]['code']

    #Getting the reel caption. There can be no caption, in that case, put or no caption on the reel
    try:
      reels_data_optimised['caption'] = reels_data[i]['caption']['text']
    except:
      reels_data_optimised['caption'] = 'No Caption on the reel'

    #Getting Video url
    reels_data_optimised['video_url'] = reels_data[i]['video_url']

    #Getting Video Duration
    reels_data_optimised['video_duration'] = reels_data[i]['video_duration']

    #Getting Posting Date
    reels_data_optimised['posting_date'] = datetime.fromtimestamp(reels_data[i]['taken_at']).strftime("%Y-%m-%d")

    #Getting the Audio flag
    reels_data_optimised['has_audio'] = reels_data[i]['has_audio']

    #Getting the reel play_count
    try:
      reels_data_optimised['play_count'] = reels_data[i]['play_count']
    except:
      reels_data_optimised['play_count'] = 0

    #Getting the reel like_count
    try:
      reels_data_optimised['like_count'] = reels_data[i]['like_count']
    except:
      reels_data_optimised['like_count'] = 0

    #Getting the reel share_count
    try:
      reels_data_optimised['share_count'] = reels_data[i]['share_count']
    except:
      reels_data_optimised['share_count'] = 0

    df = pd.concat([df, pd.DataFrame([reels_data_optimised])], ignore_index = True)

  return df



In [ ]:
reel_topic = 'Valorant'
reels_data_extracted = reels_extract(reel_topic)

In [ ]:
reels_data_extracted.head()

shortcode                                            caption  \
0  DFs0PmAxOwb  fatedsx official #valorant #valorantedit #reyn...   
1  DFshNxbIcLR         yoru ile nasıl oynanır izleyin...#valorant   
2  DEe6Km_IJ3w  Valorant is all about timing #valorantclip #va...   
3  DDkKafsKwUq                   Texture Please explain #valorant   
4  DEhXUzMzSoj           Tejo in Action. #valorant #valorantclips   

                                           video_url  video_duration  \
0  https://scontent-dus1-1.cdninstagram.com/o1/v/...          20.900   
1  https://scontent-dus1-1.cdninstagram.com/o1/v/...          28.490   
2  https://scontent-dus1-1.cdninstagram.com/o1/v/...          32.281   
3  https://scontent-dus1-1.cdninstagram.com/o1/v/...          27.908   
4  https://scontent-dus1-1.cdninstagram.com/o1/v/...          35.666   

  posting_date  has_audio  play_count  like_count  share_count  
0   2025-02-05       True     1657070      185131        39733  
1   2025-02-05       True     2367238       43754         7102  
2   2025-01-06       True     2761803      184485        51011  
3   2024-12-14       True     1791363      192237        63524  
4   2025-01-07       True     5673954      251467        96315

#Saving Data to the SQL Table (Creating a Data Pipeline and Database for later use)

In [ ]:
'''
#Convert the Pandas DataFrame to Spark DataFrame
spark_reels_data_extracted = spark.createDataFrame(reels_data_extracted)
'''

'\n#Convert the Pandas DataFrame to Spark DataFrame\nspark_reels_data_extracted = spark.createDataFrame(reels_data_extracted)\n'

In [ ]:
'''
#There are 2 ways of creating a Database table. One is a temporary view which can be done by .createOrReplaceTempView('Table_name'). This creates a temporary table. However for the persisted usgae, this table can't be used and we need a permanent table. Following is the way to create a permanent table

#Creating a permanent table
spark_reels_data_extracted.write.mode("overwrite").saveAsTable("Reels_Data_Extracted_Table")
'''

'\n#There are 2 ways of creating a Database table. One is a temporary view which can be done by .createOrReplaceTempView(\'Table_name\'). This creates a temporary table. However for the persisted usgae, this table can\'t be used and we need a permanent table. Following is the way to create a permanent table\n\n#Creating a permanent table\nspark_reels_data_extracted.write.mode("overwrite").saveAsTable("Reels_Data_Extracted_Table")\n'

In [ ]:
'''
#To use the table, we use the following syntax, such that outside is the API call to the spark server with spark.sql("SQL Query"). SQL Query is written as a normal Postgresql query.

Saved_table = spark.sql("SELECT * FROM Reels_Data_Extracted_Table").show()
'''

'\n#To use the table, we use the following syntax, such that outside is the API call to the spark server with spark.sql("SQL Query"). SQL Query is written as a normal Postgresql query.\n\nSaved_table = spark.sql("SELECT * FROM Reels_Data_Extracted_Table").show()\n'

#Video Analysis Code Starts from here

#Installing Together AI, Whisper Package and other dependencies


In [ ]:
pip install together

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.5/80.5 kB 6.3 MB/s eta 0:00:00


In [ ]:
pip install -U openai-whisper

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 800.5/800.5 kB 33.4 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 43.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 62.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 45.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 24.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 783.2 kB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 11.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.2 MB

In [ ]:
pip install moviepy

In [ ]:
import os                       #For File operations
import json
import requests
import cv2                      #For reading the video into frames
import base64                   #For reading the image frames into string
from together import Together   #For calling the Together AI API
from moviepy.editor import AudioFileClip
import whisper

  if event.key is 'enter':



In [ ]:
#Setting up the Together AI API
Together_AI_API = '<Together_AI_API_KEY>'
client = Together(api_key = Together_AI_API)

#Now we can create a client.chat.completion.create in a function where image data is given as input

In [ ]:
#Loading Whisper Model:
model = whisper.load_model("base")

100%|████████████████████████████████████████| 139M/139M [00:00<00:00, 146MiB/s]
  checkpoint = torch.load(fp, map_location=device)



#Important Function Definitions

Function to Download a video

In [ ]:
def video_download(url, save_path):
  print(f'Downloading Video: ', url)
  response = requests.get(url)
  if response.status_code == 200:
    #Using os package, we open the file in write mode and write the video data in chunks of 1024 bytes
    with open(save_path, 'wb') as file:
      for chunk in response.iter_content(chunk_size = 1024):
        if chunk:
          file.write(chunk)
  else:
    print("Video download unsuccessful. Error: ", response.status_code)


In [ ]:
def video_to_audio(video_path, audio_path):
  with AudioFileClip(video_path) as video:
    video.write_audiofile(audio_path)
  return audio_path

In [ ]:
def transcribe_audio(audio_path):
  result = model.transcribe(audio_path)
  return result['text']

Function to get the frame by frame data

In [ ]:
def video_splitter(video_path, num_of_frames):
  cap = cv2.VideoCapture(video_path)
  if cap.isOpened():
    #Getting the total number of frames in a video
    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT)) #Function to obtain the framecount of the video

    #Calculating the frame intervals
    frame_indices = [int(i* total_frames/num_of_frames) for i in range(num_of_frames)]

    frames_base64 = []
    i = 1
    #We have the frames that we want to capture. We loop it in a for loop,
    #set the video capture to that frame and get the image data in buffer as jpg file
    #Then we encode is as base64. However, as per together ai syntax, we need base64
    #input as >>> data:image/jpeg;base64,{base64}
    for frames in frame_indices:
      cap.set(cv2.CAP_PROP_POS_FRAMES, frames-1) #Setting the device to the designated frame
      ret, frame = cap.read()
      if ret:
        ret2, buffer = cv2.imencode('.jpg', frame)
        if ret2:
          print(f'Reading frame {i}')
          image_bs64 = base64.b64encode(buffer).decode('utf-8')
          image_bs64_string = f'data:image/jpeg;base64,{image_bs64}'
          frames_base64.append(image_bs64_string)
        i+=1

    print('Number of frames extracted: ', len(frames_base64))

    print('\n')
    print()
  else:
    print('Video not opened')

  return frames_base64



  '''
  #Now we will run the entire video, frame by frame. ret will have a boolean value
  #while frame will have the image data for a specific frame
  ret, frame = cap.read()
  while ret:
    if current_frame in frame_indices:
      #If current_frame in frame_indices, we save the image in a base64 format
      #and the image string data is passed to frames_base64
      ret2, buffer = cv2.imencode('.jpg', frame)
      if ret2:
        image_bs64 = base64.b64encode(buffer).decode('utf-8')
        image_bs64_string = f'data:image/jpeg;base64,{image_bs64}'
        frames_base64.append(image_bs64_string)
    current_frame += 1
    ret, frame = cap.read()
    cap.set(cv2.CAP_PROP_POS_FRAMES, current_frame)
  '''

Function for frame image analysis

In [ ]:
def video_analysis_from_frames_list(frames_base64_list, caption):
  #Setting up the client.chats.completion.create >>> Refer the API Documentation or Playground for code
  i = 0
  video_data = ''
  for frames in frames_base64_list:
    print(f'Analysing frame {i}')
    response = client.chat.completions.create(
        model = 'meta-llama/Llama-Vision-Free',
        messages = [
          {
                "role": "system",
                "content": "<human>: Hi! <bot>: I am a social media reels analyzer. I analyze different game reels, memes, etc. I am careful to only provide factual answers, pertaining to the game's lingo or internal game terms and when I’m not sure of the answer I say “Sorry, I don’t have an answer for you on that. Sorry I wasn’t able to help!” and add basic description of the image. Note that you have to provide an output within the 50-150 word range maximum."
          },
          {
                "role": "user",
                "content": [
                              {
                                "type": "text",
                                "text": f"Provide me the video frame analysis for the video frame picked up from an Instagram reel. Note that we are analysing for a game named Valorant. \n\nIf some of the terms in the video frame are unknown to you, mention that it is unknown with a basic description of what is visible in the frame. If the images have known valorant related content, then provide the valorant specific details. \n\nNote that there are multiple image frames that are being analyzed and this is one of the frames in a specific reel. All the analysis for the frames will be consolidated and passed into a large language model along with audio transcription for detailed summarisation. Here's the caption: {caption}. Note that the analysis per frame is within 50 to 150 words"
                              },
                              {
                                  "type": "image_url",

                                  "image_url":
                                   {
                                        "url": f"{frames}"

                                  },
                              },
                ]
          }
        ],
        #stream = True
    )
    # We take the content from response.choices[0].message.content
    #If we use stream = True in completitions, we have to use chunk to concat the response first, as part part data is sent while processing. We use chunk.choices[0].message.content += chunk.choices[0].message.content to get a response.choices[0].message.content
    video_data = video_data + f'\nAnalysing equally spaced video frame {i}: \n' + response.choices[0].message.content  # Access choices from the chunk
    i+=1
    print(video_data)

  return video_data

#Main Function Definition for calling Video Data Analysis

In [ ]:
def frame_by_frame_video_text_analysis(reels_data_extracted):
  video_url_list = [reels_data_extracted[['video_url']]]
  print(video_url_list)
  video_data_scanned = pd.DataFrame()
  #Analysing reels one by one
  for i in range(len(reels_data_extracted)):
    analysis_dict = {}
    single_video_url = reels_data_extracted['video_url'][i]
    print(f'\nAnalysing reel: {single_video_url}')
    video_download(single_video_url, 'video.mp4')

    print('\nConverting Video to Audio')
    video_to_audio('video.mp4', 'audio.mp3')

    print('\nTranscribing Audio')
    transcription = transcribe_audio('audio.mp3')
    print(transcription)


    print('\nExtracting Frames')
    video_duration = reels_data_extracted['video_duration'][reels_data_extracted['video_url'] == single_video_url]
    frames_base64_list = video_splitter('video.mp4', int(video_duration))

    print('\nAnalysing Frames one by one with caption:')
    caption = reels_data_extracted['caption'][reels_data_extracted['video_url'] == single_video_url]
    print(str(caption))
    video_data = video_analysis_from_frames_list(frames_base64_list, caption)
    reels_data_extracted['video_analysis'] = video_data
    print(video_data)

    print('Saving Video Data')
    analysis_dict['video_url'] = single_video_url #Maps Video url to video data
    analysis_dict['video_transcription'] = transcription
    analysis_dict['video_data'] = video_data
    analysis_dict['video_duration_int'] = video_duration
    video_data_scanned = pd.concat([video_data_scanned, pd.DataFrame([analysis_dict])], ignore_index = True)


  return video_data_scanned


#Function call for Reel data analysis

In [ ]:
video_data_extracted = frame_by_frame_video_text_analysis(reels_data_extracted)
video_data_extracted.head()

[                                            video_url
0   https://scontent-dus1-1.cdninstagram.com/o1/v/...
1   https://scontent-dus1-1.cdninstagram.com/o1/v/...
2   https://scontent-dus1-1.cdninstagram.com/o1/v/...
3   https://scontent-dus1-1.cdninstagram.com/o1/v/...
4   https://scontent-dus1-1.cdninstagram.com/o1/v/...
5   https://scontent-dus1-1.cdninstagram.com/o1/v/...
6   https://scontent-dus1-1.cdninstagram.com/o1/v/...
7   https://scontent-dus1-1.cdninstagram.com/o1/v/...
8   https://scontent-dus1-1.cdninstagram.com/o1/v/...
9   https://scontent-dus1-1.cdninstagram.com/o1/v/...
10  https://scontent-dus1-1.cdninstagram.com/o1/v/...
11  https://scontent-dus1-1.cdninstagram.com/o1/v/...]

Analysing reel: https://scontent-dus1-1.cdninstagram.com/o1/v/t16/f2/m86/AQNBofDdN35VTFqGKFo9vfWd6tuQi4nBIDzNmp1Lwyei4T-ROoO3Xloo6jsjVvuM5K7Pr6rDBR5uSyvVJ4ztX_FCIKSCJfFnymagiH8.mp4?efg=eyJ4cHZfYXNzZXRfaWQiOjExMjU0NjIyNDI2MTE3NjIsInZlbmNvZGVfdGFnIjoieHB2X3Byb2dyZXNzaXZlLklOU1RBR1JBTS5DTElQUy5DMy

  warnings.warn("FP16 is not supported on CPU; using FP32 instead")



MoviePy - Done.

Transcribing Audio


  frames_base64_list = video_splitter('video.mp4', int(video_duration))



 e aí

Extracting Frames
Reading frame 1
Reading frame 2
Reading frame 3
Reading frame 4
Reading frame 5
Reading frame 6
Reading frame 7
Reading frame 8
Reading frame 9
Reading frame 10
Reading frame 11
Reading frame 12
Reading frame 13
Reading frame 14
Reading frame 15
Reading frame 16
Reading frame 17
Reading frame 18
Reading frame 19
Reading frame 20
Number of frames extracted:  20




Analysing Frames one by one with caption:
0    fatedsx official #valorant #valorantedit #reyn...
Name: caption, dtype: object
Analysing frame 0

Analysing equally spaced video frame 0: 
The image depicts a Valorant player with a malevolent grin, donning a yellow-and-white Splendid Screen short-sleeved shirt paired with black shorts. The player's attire is complemented by a black and yellow 'VALORANT' logo-emblazoned baseball cap and a pair of white sneakers.

The frame showcases a dark and ominous background, with a subtle hint of a brownish-yellow wall. The overall atmosphere is muted, with a predomi

...

  warnings.warn("FP16 is not supported on CPU; using FP32 instead")



MoviePy - Done.

Transcribing Audio


  frames_base64_list = video_splitter('video.mp4', int(video_duration))



Streaming output truncated to the last 5000 lines.
The image shows a screenshot from the game Valorant, with two players facing each other in a round-robin game. The player on the left is wearing a red hat and a blue shirt, while the player on the right is wearing a blue hat and a green shirt. The player on the left is holding a gun and aiming at the player on the right, who is also holding a gun and aiming back.

The text "did they just find the new meta?" is written in white and yellow letters at the top of the image, suggesting that the players may have discovered a new strategy or gameplay style that gives them an advantage. The background of the image is blurry, but it appears to be a map or level from the game.

Overall, the image suggests that the players are engaged in a competitive match of Valorant, and are trying to outmaneuver each other to gain the upper hand. The text "did they just find the new meta?" implies that the players may have discovered a new strategy or gamepla

video_url  \
0  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
1  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
2  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
3  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
4  https://scontent-dus1-1.cdninstagram.com/o1/v/...   

                                 video_transcription  \
0                                               e aí   
1                                                      
2               今日生活頃に終了君のあ actまじでそんな物故なの slide削 Hit   
3   Not long, they always have to play the maximu...   
4                                 總共12.EDthnetoc哈哈哈武   

                                          video_data  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nI'...   

                                 video_duration_int  
0    0    20.9
Name: video_duration, dtype: float64  
1   1    28.49
Name: video_duration, dtype: float64  
2  2    32.281
Name: video_duration, dtype: float64  
3  3    27.908
Name: video_duration, dtype: float64  
4  4    35.666
Name: video_duration, dtype: float64

In [ ]:
# Assuming both dataframes have a 'video_url' column
merged_data = pd.merge(video_data_extracted, reels_data_extracted, on='video_url', how='inner')
merged_data.head()


video_url  \
0  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
1  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
2  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
3  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
4  https://scontent-dus1-1.cdninstagram.com/o1/v/...   

                                 video_transcription  \
0                                               e aí   
1                                                      
2               今日生活頃に終了君のあ actまじでそんな物故なの slide削 Hit   
3   Not long, they always have to play the maximu...   
4                                 總共12.EDthnetoc哈哈哈武   

                                          video_data  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nI'...   

                                 video_duration_int    shortcode  \
0    0    20.9
Name: video_duration, dtype: float64  DFs0PmAxOwb   
1   1    28.49
Name: video_duration, dtype: float64  DFshNxbIcLR   
2  2    32.281
Name: video_duration, dtype: float64  DEe6Km_IJ3w   
3  3    27.908
Name: video_duration, dtype: float64  DDkKafsKwUq   
4  4    35.666
Name: video_duration, dtype: float64  DEhXUzMzSoj   

                                             caption  video_duration  \
0  fatedsx official #valorant #valorantedit #reyn...          20.900   
1         yoru ile nasıl oynanır izleyin...#valorant          28.490   
2  Valorant is all about timing #valorantclip #va...          32.281   
3                   Texture Please explain #valorant          27.908   
4           Tejo in Action. #valorant #valorantclips          35.666   

  posting_date  has_audio  play_count  like_count  share_count  \
0   2025-02-05       True     1657070      185131        39733   
1   2025-02-05       True     2367238       43754         7102   
2   2025-01-06       True     2761803      184485        51011   
3   2024-12-14       True     1791363      192237        63524   
4   2025-01-07       True     5673954      251467        96315   

                                      video_analysis  
0  \nAnalysing equally spaced video frame 0: \nTh...  
1  \nAnalysing equally spaced video frame 0: \nTh...  
2  \nAnalysing equally spaced video frame 0: \nTh...  
3  \nAnalysing equally spaced video frame 0: \nTh...  
4  \nAnalysing equally spaced video frame 0: \nTh...

#Converting the Merged Data into a Databricks Table for later usage

In [ ]:
'''
#Convert the Pandas DataFrame to Spark DataFrame
video_data_merged_extracted = spark.createDataFrame(merged_data)
'''

'\n#Convert the Pandas DataFrame to Spark DataFrame\nvideo_data_merged_extracted = spark.createDataFrame(merged_data)\n'

In [ ]:
'''
#There are 2 ways of creating a Database table. One is a temporary view which can be done by .createOrReplaceTempView('Table_name'). This creates a temporary table. However for the persisted usgae, this table can't be used and we need a permanent table. Following is the way to create a permanent table

#Creating a permanent table
spark_video_data_merged_extracted.write.mode("overwrite").saveAsTable("Video_Data_Merge_Extracted")
'''

'\n#There are 2 ways of creating a Database table. One is a temporary view which can be done by .createOrReplaceTempView(\'Table_name\'). This creates a temporary table. However for the persisted usgae, this table can\'t be used and we need a permanent table. Following is the way to create a permanent table\n\n#Creating a permanent table\nspark_video_data_merged_extracted.write.mode("overwrite").saveAsTable("Video_Data_Merge_Extracted")\n'

In [ ]:
'''
#To use the table, we use the following syntax, such that outside is the API call to the spark server with spark.sql("SQL Query"). SQL Query is written as a normal Postgresql query.

Saved_video_table = spark.sql("SELECT * FROM Video_Data_Merge_Extracted").show()
'''

'\n#To use the table, we use the following syntax, such that outside is the API call to the spark server with spark.sql("SQL Query"). SQL Query is written as a normal Postgresql query.\n\nSaved_video_table = spark.sql("SELECT * FROM Video_Data_Merge_Extracted").show()\n'

#Getting Comment Data and setting up the dependencies

Setting Rapidapi for comments extraction

In [ ]:
comments_url = "https://instagram-scraper-api2.p.rapidapi.com/v1/comments"

comment_headers = {
	"x-rapidapi-key": "<API-KEY>",
	"x-rapidapi-host": "instagram-scraper-api2.p.rapidapi.com"
}

In [ ]:
def shortcode_comments_deprecated(shortcode, comments_count):
  if comments_count > 0:
    comments_data = pd.DataFrame()
    comments_querystring = {'code_or_id_or_url' : shortcode, 'sort_by': 'popular'}
    response = requests.get(comments_url, headers = comment_headers, params = comments_querystring)
    if response.status_code == 200:
      comments_data = response.json()
      comments_data = comments_data['data']['items']

  comments_querystring = {'code_or_id_or_url' : shortcode, 'sort_by': 'popular'}
  response = requests.get(comments_url, headers = comment_headers, params = comments_querystring)

In [ ]:
'''
def get_comments_df_deprecated(merged_data, comments_count):
  comments_data = pd.DataFrame()
  for shortcode in merged_data['shortcode']:

'''

"\ndef get_comments_df_deprecated(merged_data, comments_count):\n  comments_data = pd.DataFrame()\n  for shortcode in merged_data['shortcode']:\n\n"

In [ ]:
#from genericpath import exists
def shortcode_comments(shortcode, comments_count):
  comments_data_list = []
  while comments_count > 0:
    comments_querystring = {'code_or_id_or_url' : shortcode, 'sort_by': 'popular'}
    response = requests.get(comments_url, headers = comment_headers, params = comments_querystring)
    if response.status_code == 200:
      comments_data = response.json()

      try:
        pagination_token = comments_data['data']['pagination_token']
      except:
        pagination_token = ''

      comments_data = comments_data['data']['items']
      comments_data_extracted_list = [comments_data[i]['text'] for i in range(len(comments_data))]
      comments_data_list.append(comments_data_extracted_list)
      comments_count = comments_count - len(comments_data)
      print(f'Comments count: {comments_count}')

      #How to use an apply function call to get 2 outputs for 1 single row of a dataframe
      try:
        if pagination_token != '' & comments_count > 0:
          call_api = True
        else:
          call_api = False
      except:
        call_api = False

      if call_api == True:
        comments_querystring = {'code_or_id_or_url' : shortcode, 'sort_by': 'popular', 'pagination_token': comments_data['data']['pagination_token']}
      else:
        return comments_data_list
    else:
      raise ("API error", response.status_code)

#Function call for List of comments

In [ ]:
merged_data['comments'] = merged_data['shortcode'].apply(lambda x: shortcode_comments(x, 25))

Comments count: 11
Comments count: 10
Comments count: 10
Comments count: 10
Comments count: 12
Comments count: 10
Comments count: 10
Comments count: 10
Comments count: 10
Comments count: 10
Comments count: 10
Comments count: 10


In [ ]:
merged_data.head()

video_url  \
0  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
1  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
2  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
3  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
4  https://scontent-dus1-1.cdninstagram.com/o1/v/...   

                                 video_transcription  \
0                                               e aí   
1                                                      
2               今日生活頃に終了君のあ actまじでそんな物故なの slide削 Hit   
3   Not long, they always have to play the maximu...   
4                                 總共12.EDthnetoc哈哈哈武   

                                          video_data  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nI'...   

                                 video_duration_int    shortcode  \
0    0    20.9
Name: video_duration, dtype: float64  DFs0PmAxOwb   
1   1    28.49
Name: video_duration, dtype: float64  DFshNxbIcLR   
2  2    32.281
Name: video_duration, dtype: float64  DEe6Km_IJ3w   
3  3    27.908
Name: video_duration, dtype: float64  DDkKafsKwUq   
4  4    35.666
Name: video_duration, dtype: float64  DEhXUzMzSoj   

                                             caption  video_duration  \
0  fatedsx official #valorant #valorantedit #reyn...          20.900   
1         yoru ile nasıl oynanır izleyin...#valorant          28.490   
2  Valorant is all about timing #valorantclip #va...          32.281   
3                   Texture Please explain #valorant          27.908   
4           Tejo in Action. #valorant #valorantclips          35.666   

  posting_date  has_audio  play_count  like_count  share_count  \
0   2025-02-05       True     1657070      185131        39733   
1   2025-02-05       True     2367238       43754         7102   
2   2025-01-06       True     2761803      184485        51011   
3   2024-12-14       True     1791363      192237        63524   
4   2025-01-07       True     5673954      251467        96315   

                                      video_analysis  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nTh...   

                                            comments  
0  [[Irmão que delicinha de edit, Almost made Val...  
1  [[Reis direk vursana malmısın awl, Bro is play...  
2  [[Let's talk about how cypher missed the first...  
3  [[Credit: @caimssy1.1, , , And he did this twi...  
4  [[what the Yoru doin, Tejo=sova+breach+brim+ka...

In [ ]:
str(merged_data['comments'][1])

'[[\'Reis direk vursana malmısın awl\', \'Bro is playing 5d chess in valorant😭\', \'cake fhinese video\', \'\', \'“matar logo ou traumatizar?”\\n \\nEle:\', \'🔥\', \'Mal\', \'Bravo arda 👏👏\', \'As vezes o cara é um CLT querendo jogar uma para passar o tempo\', \'Skor hep 5-6 falan bi de hep 1vs1\', \'Yada bir bıçak atıp yolunuza bakabilirsiniz arkadaşlar\', \'\', \'"Bütün skillerini rakiple dalga geçmeye harcıyor" demeyelim diye artık son turda yaptığı klipleri atıyor\', \'\', \'\']]'

# Defining Analysis LLM to perform Relevance and Sentiment Analysis


In [ ]:
pip install openai

In [ ]:
import openai

In [ ]:
#Setting up the Together AI API
OPENAI_API = 'OPEN_AI_KEY'
client_openai = openai.OpenAI(api_key=OPENAI_API)


In [ ]:
def analysis_llm(video_data, video_transcription, comments, prompt):
  #Setting up the client.chats.completion.create >>> Refer the API Documentation or Playground for code
  response = client_openai.chat.completions.create(
        model = 'gpt-4o-mini',
        messages = [
          {
                "role": "system",
                "content": '''
                              I am a social media reels analyzer. I check the video analysis, video transcription and comments to check for relevance and sentiment.
                              When asked for sentiment, I check whether the comments are positive or negative. Furthermore, I check what is the mood of the sentiment.
                              For example, within a positive sentiment, moods can be excited, happy, cheerful, etc. and within a negative sentiments, moods can be sad, angry, frustrated, etc.
                              Once the mood is found, I give 1 WORD OUTPUT for the mood as the comments sentiment of the people to the reel.
                              NOTE: IF ASKED FOR SENTIMENT, THE OUTPUT SHOULD BE THE MOOD AND THIS OUTPUT SIZE WILL BE 1 WORD ONLY. NO MORE THAN 1 WORD.
                              Output for sentiment should look like:

                              Sentiment: <Sentiment>
                              Mood: <Mood>
                              Sentiment Reasoning: <Sentiment Reasoning>

                              Sentiment can be positive, negative or neutral and mood can be happy, sad, angry, excited, frustrated, confused, etc.
                              Sentiment Reasoning provides the reasoning for the sentiment and mood assigned in 20-25 WORDS MAX. No more than 25 words for sentiment reasoning.
                              NOTE: <Sentiment>, <Mood> have only 1 WORD OUTPUTs. NO MORE THAN 1 WORD.

                              When asked for relevance, I check whether the comments are discussing any topic associated with something within the comments and the video.
                              Also try to reasoning what type of response would the topic discussed within the would have. Based on the obtaied reasoning, if the mood or sentiment in the comments is same as the one obtained from reasoning, the topic is relevant.
                              If after reasoning from an viewers perspective, the response or mood or sentiment from comments has opposite output as the one obtained from reasoning, then the topic is not relevant.
                              Thus, the output for relevance should look like:

                              Relevance: <Relevance>
                              Relevance Reasoning: <Relevance Reasoning>

                              Relevance can be relevant or not relevant.
                              Relevance Reasoning provides the reasoning for the relevance and topic discussed in 20-25 WORDS MAX. No more than 25 words for relevance reasoning.
                              NOTE: <Relevance> have only 1 WORD OUTPUTs. NO MORE THAN 1 WORD.

                              Over output will look like:

                              Sentiment: <Sentiment>
                              Mood: <Mood>
                              Sentiment Reasoning: <Sentiment Reasoning>
                              Relevance: <Relevance>
                              Relevance Reasoning: <Relevance Reasoning>

                              NOTE: <Sentiment>, <Mood>, <Relevance> have only 1 WORD OUTPUTs. NO MORE THAN 1 WORD.
                              <Sentiment Reasoning> and <Relevance Reasoning> have reasoning for MAX 25 words. NO MORE THAN 25 WORDS
                              '''
          },
          {
                "role": "user",
                "content": [
                              {
                                "type": "text",
                                "text": f'''
                                            Here is the video data: {video_data}
                                            Here is the video transcription: {video_transcription}
                                            Here are the comments: {comments}
                                            Here is the prompt:
                                            {prompt}

                                            NOTE: <Sentiment>, <Mood>, <Relevance> have only 1 WORD OUTPUTs. NO MORE THAN 1 WORD.
                                            '''
                              },
                ]
          }
        ],
        #stream = True
    )
    # We take the content from response.choices[0].message.content
    #If we use stream = True in completitions, we have to use chunk to concat the response first, as part part data is sent while processing. We use chunk.choices[0].message.content += chunk.choices[0].message.content to get a response.choices[0].message.content

  return response.choices[0].message.content

# Function Call for Check Analysis for Sentiment Analysis

In [ ]:
prompt = 'Check the video analysis, video transcription and comments to check for sentiment, mood and relevance. Provide me output in the mentioned format with only 1 WORD OUTPUT. Also, Reasoning should be within 25 WORDS. NO MORE THAN 25 WORDS'

In [ ]:
merged_data['sentiment_analysis'] = merged_data.apply(lambda x: analysis_llm(x['video_data'], x['video_transcription'], x['comments'], prompt), axis = 1)

In [ ]:
merged_data.head()

video_url  \
0  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
1  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
2  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
3  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
4  https://scontent-dus1-1.cdninstagram.com/o1/v/...   

                                 video_transcription  \
0                                               e aí   
1                                                      
2               今日生活頃に終了君のあ actまじでそんな物故なの slide削 Hit   
3   Not long, they always have to play the maximu...   
4                                 總共12.EDthnetoc哈哈哈武   

                                          video_data  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nI'...   

                                 video_duration_int    shortcode  \
0    0    20.9
Name: video_duration, dtype: float64  DFs0PmAxOwb   
1   1    28.49
Name: video_duration, dtype: float64  DFshNxbIcLR   
2  2    32.281
Name: video_duration, dtype: float64  DEe6Km_IJ3w   
3  3    27.908
Name: video_duration, dtype: float64  DDkKafsKwUq   
4  4    35.666
Name: video_duration, dtype: float64  DEhXUzMzSoj   

                                             caption  video_duration  \
0  fatedsx official #valorant #valorantedit #reyn...          20.900   
1         yoru ile nasıl oynanır izleyin...#valorant          28.490   
2  Valorant is all about timing #valorantclip #va...          32.281   
3                   Texture Please explain #valorant          27.908   
4           Tejo in Action. #valorant #valorantclips          35.666   

  posting_date  has_audio  play_count  like_count  share_count  \
0   2025-02-05       True     1657070      185131        39733   
1   2025-02-05       True     2367238       43754         7102   
2   2025-01-06       True     2761803      184485        51011   
3   2024-12-14       True     1791363      192237        63524   
4   2025-01-07       True     5673954      251467        96315   

                                      video_analysis  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nTh...   

                                            comments  \
0  [[Irmão que delicinha de edit, Almost made Val...   
1  [[Reis direk vursana malmısın awl, Bro is play...   
2  [[Let's talk about how cypher missed the first...   
3  [[Credit: @caimssy1.1, , , And he did this twi...   
4  [[what the Yoru doin, Tejo=sova+breach+brim+ka...   

                                  sentiment_analysis  
0  Sentiment: Positive  \nMood: Excited  \nSentim...  
1  Sentiment: Negative  \nMood: Frustrated  \nSen...  
2  Sentiment: Positive  \nMood: Amused  \nSentime...  
3  Sentiment: Positive  \nMood: Excited  \nSentim...  
4  Sentiment: Positive  \nMood: Excited  \nSentim...

In [ ]:
merged_data['sentiment_analysis'][0]

'Sentiment: Positive  \nMood: Excited  \nSentiment Reasoning: The comments express enthusiasm and admiration for the editing style with emojis and compliments, indicating a positive reception.  \nRelevance: Relevant  \nRelevance Reasoning: Comments discuss the editing quality and support for the creator, directly related to the content showcased in the video.'

In [ ]:
merged_data['sentiment_analysis'][10]

"Sentiment: Positive  \nMood: Excited  \nSentiment Reasoning: The comments express admiration, excitement for gameplay, and appreciation for the content, indicating a positive reception overall.  \nRelevance: Relevant  \nRelevance Reasoning: The comments discuss the gameplay and reactions to in-game actions, connecting directly with the video's content and context."

# Regex Function for parsing the output


Note: Regex Function should be used only when the pattern for outputs is fixed. We can also use parse function available in the open ai documentations on the net. Pydantic can also be used for parsing the output and it can be provide better results, in case the output doesn't follow a proper pattern.

In [ ]:
# prompt: Define an regex function that can be used to extract sentiment, mood and relevance from the dataframe into 3 different variables.
# Google Gemini was used for the regex function (AI is used for some of the function calls as well. But most of it is typed or hand written)

import pandas as pd
import re

def extract_sentiment_mood_relevance(text):
    """
    Extracts sentiment, mood, and relevance from text using regex.

    Args:
        text: The input text string.

    Returns:
        A tuple containing sentiment, mood, and relevance, or None if not found.
    """
    sentiment_match = re.search(r"Sentiment:\s*(\w+)", text)
    mood_match = re.search(r"Mood:\s*(\w+)", text)
    relevance_match = re.search(r"Relevance:\s*(\w+)", text)

    if sentiment_match and mood_match and relevance_match:
        sentiment = sentiment_match.group(1)
        mood = mood_match.group(1)
        relevance = relevance_match.group(1)
        return sentiment, mood, relevance
    else:
        return None

# Example usage with your DataFrame:
merged_data['extracted_data'] = merged_data['sentiment_analysis'].apply(extract_sentiment_mood_relevance)

# Further processing
merged_data[['sentiment', 'mood', 'relevance']] = pd.DataFrame(merged_data['extracted_data'].tolist(), index= merged_data.index)

#Now you can use these columns
print(merged_data[['sentiment', 'mood', 'relevance']])


   sentiment        mood relevance
0   Positive     Excited  Relevant
1   Negative  Frustrated  Relevant
2   Positive      Amused  Relevant
3   Positive     Excited  Relevant
4   Positive     Excited  Relevant
5   Negative  Frustrated  Relevant
6   Negative  Frustrated  Relevant
7   Positive    Cheerful  Relevant
8   Negative  Frustrated  Relevant
9   Positive       Happy  Relevant
10  Positive     Excited  Relevant
11  Positive     Excited  Relevant


In [ ]:
merged_data.head()

video_url  \
0  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
1  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
2  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
3  https://scontent-dus1-1.cdninstagram.com/o1/v/...   
4  https://scontent-dus1-1.cdninstagram.com/o1/v/...   

                                 video_transcription  \
0                                               e aí   
1                                                      
2               今日生活頃に終了君のあ actまじでそんな物故なの slide削 Hit   
3   Not long, they always have to play the maximu...   
4                                 總共12.EDthnetoc哈哈哈武   

                                          video_data  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nI'...   

                                 video_duration_int    shortcode  \
0    0    20.9
Name: video_duration, dtype: float64  DFs0PmAxOwb   
1   1    28.49
Name: video_duration, dtype: float64  DFshNxbIcLR   
2  2    32.281
Name: video_duration, dtype: float64  DEe6Km_IJ3w   
3  3    27.908
Name: video_duration, dtype: float64  DDkKafsKwUq   
4  4    35.666
Name: video_duration, dtype: float64  DEhXUzMzSoj   

                                             caption  video_duration  \
0  fatedsx official #valorant #valorantedit #reyn...          20.900   
1         yoru ile nasıl oynanır izleyin...#valorant          28.490   
2  Valorant is all about timing #valorantclip #va...          32.281   
3                   Texture Please explain #valorant          27.908   
4           Tejo in Action. #valorant #valorantclips          35.666   

  posting_date  has_audio  play_count  like_count  share_count  \
0   2025-02-05       True     1657070      185131        39733   
1   2025-02-05       True     2367238       43754         7102   
2   2025-01-06       True     2761803      184485        51011   
3   2024-12-14       True     1791363      192237        63524   
4   2025-01-07       True     5673954      251467        96315   

                                      video_analysis  \
0  \nAnalysing equally spaced video frame 0: \nTh...   
1  \nAnalysing equally spaced video frame 0: \nTh...   
2  \nAnalysing equally spaced video frame 0: \nTh...   
3  \nAnalysing equally spaced video frame 0: \nTh...   
4  \nAnalysing equally spaced video frame 0: \nTh...   

                                            comments  \
0  [[Irmão que delicinha de edit, Almost made Val...   
1  [[Reis direk vursana malmısın awl, Bro is play...   
2  [[Let's talk about how cypher missed the first...   
3  [[Credit: @caimssy1.1, , , And he did this twi...   
4  [[what the Yoru doin, Tejo=sova+breach+brim+ka...   

                                  sentiment_analysis  \
0  Sentiment: Positive  \nMood: Excited  \nSentim...   
1  Sentiment: Negative  \nMood: Frustrated  \nSen...   
2  Sentiment: Positive  \nMood: Amused  \nSentime...   
3  Sentiment: Positive  \nMood: Excited  \nSentim...   
4  Sentiment: Positive  \nMood: Excited  \nSentim...   

                     extracted_data sentiment        mood relevance  
0     (Positive, Excited, Relevant)  Positive     Excited  Relevant  
1  (Negative, Frustrated, Relevant)  Negative  Frustrated  Relevant  
2      (Positive, Amused, Relevant)  Positive      Amused  Relevant  
3     (Positive, Excited, Relevant)  Positive     Excited  Relevant  
4     (Positive, Excited, Relevant)  Positive     Excited  Relevant